
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning" style="width: 600px">
</div>




# Training with Pandas Function API

This notebook demonstrates how to use Pandas Function API to manage and scale machine learning models for IoT devices. 

## ![Spark Logo Tiny](https://files.training.databricks.com/images/105/logo_spark_tiny.png) Learning Objectives:<br>

By the end of this lesson, you should be able to;

* Defines a pandas functions and apply it to a model
* Use <a href="https://spark.apache.org/docs/latest/api/python/reference/pyspark.sql/api/pyspark.sql.GroupedData.applyInPandas.html" target="_blank"> **.groupBy().applyInPandas()** </a> to build many models in parallel
* Serve multiple models from a registered model

## 📌 Requirements

**Required Databricks Runtime Version:** 
* Please note that in order to run this notebook, you must use one of the following Databricks Runtime(s): **12.2.x-cpu-ml-scala2.12**

## Lesson Setup

The first thing we're going to do is to **run setup script**. This script will define the required configuration variables that are scoped to each user.

In [0]:
%run ./Includes/Classroom-Setup

Python interpreter will be restarted.
Python interpreter will be restarted.


Resetting the learning environment:
| No action taken

Skipping install of existing datasets to "dbfs:/mnt/dbacademy-datasets/scalable-machine-learning-with-apache-spark/v02"

Validating the locally installed datasets:
| listing local files...(2 seconds)
| validation completed...(2 seconds total)

Creating & using the schema "charlie_ohara_4mi2_da_sml" in the catalog "hive_metastore"...(1 seconds)

Predefined tables in "charlie_ohara_4mi2_da_sml":
| -none-

Predefined paths variables:
| DA.paths.working_dir: dbfs:/mnt/dbacademy-users/charlie.ohara@standard.ai/scalable-machine-learning-with-apache-spark
| DA.paths.user_db:     dbfs:/mnt/dbacademy-users/charlie.ohara@standard.ai/scalable-machine-learning-with-apache-spark/database.db
| DA.paths.datasets:    dbfs:/mnt/dbacademy-datasets/scalable-machine-learning-with-apache-spark/v02

Setup completed (7 seconds)



## Create a Spark DataFrame

Create dummy data with:
- **`device_id`**: 10 different devices
- **`record_id`**: 10k unique records
- **`feature_1`**: a feature for model training
- **`feature_2`**: a feature for model training
- **`feature_3`**: a feature for model training
- **`label`**: the variable we're trying to predict

In [0]:
import pyspark.sql.functions as f

# create sythetic aka BS data 
df = (spark
      .range(1000*100)
      .select(f.col("id").alias("record_id"), (f.col("id")%10).alias("device_id"))
      .withColumn("feature_1", f.rand() * 1)
      .withColumn("feature_2", f.rand() * 2)
      .withColumn("feature_3", f.rand() * 3)
      .withColumn("label", (f.col("feature_1") + f.col("feature_2") + f.col("feature_3")) + f.rand())
     )

display(df)

record_id device_id feature_1 feature_2 feature_3 label 0 0 0.5913269812644489 1.112624479962482 0.9383567332587058 3.599200876731657 1 1 0.2472129573119317 1.339393994322151 0.36354489657515054 2.8284911486508206 2 2 0.05249232681429028 1.2435866204951875 1.48153079167651 2.899007213485999 3 3 0.36458761315688115 0.583744962019102 0.7329966016597367 2.165171666135468 4 4 0.552657693182898 1.7127538422257746 1.4460135454232481 4.382039674422539 5 5 0.2731973411636208 1.2702604513854396 0.6874138777647782 2.395843585005227 6 6 0.004520761335917056 1.2435503189591823 0.30919173138981304 2.0764288822250303 7 7 0.8191065070385846 0.34956610867400784 2.210135357499151 4.005836631215531 8 8 0.9984137037595777 0.8510422700126778 2.5389794995472412 5.233024923012909 9 9 0.2480896138905483 1.2971139690365017 1.9046794438060033 4.367748918180926 10 0 0.7993587204447464 0.9496071751293982 0.9716470575072201 3.192090815718112 11 1 0.6294933662195203 1.321679146066587 1.897314445209496 4.4948571501827495 12 2 0.9022222044409527 0.44485056692308844 1.1238051714403847 2.5524705795156564 13 3 0.35331546536154745 0.46123252640733226 0.15177055154348928 1.5002508373463523 14 4 0.9284481010133068 1.8752476396332964 1.6236642280554365 4.710951716756325 15 5 0.10268950917828068 1.4089971662510619 2.6325352798019384 4.825489574099577 16 6 0.8424168156663638 1.7648663212880467 0.5884819083950933 4.128628695164525 17 7 0.7644918536430274 0.4695050621126722 0.8924839768993923 2.5207639672082816 18 8 0.17378291220403685 1.7294691670005007 0.5459175037955648 2.514707959382351 19 9 0.753112742058177 0.47027872355054257 2.1657587699996315 4.141008048549111 20 0 0.20206847535845873 1.4533651926489255 2.1343334937634477 4.388630687001344 21 1 0.38129423776569327 0.6940469797271798 0.010877859521410627 1.4764811668173103 22 2 0.11425866414756869 0.05591141853773918 2.6047015653035968 2.9746133315436505 23 3 0.11030521139957328 1.7482853295127747 2.864963901207933 4.762889818419795 24 4 0.8290851573280731 1.1197658638073715 0.01633550453387811 2.02080783631116 25 5 0.8580651283427368 0.18801153748954635 1.6615015257119419 3.452149761984669 26 6 0.9142169533003828 1.4161960204788437 2.4769945671068454 5.0150669339257234 27 7 0.42815773462212103 1.028463075884599 2.0715659231316463 4.474465672556487 28 8 0.09661065420940729 1.314202758851371 1.6740628266924567 3.276568342342539 29 9 0.48364319458916105 1.5259207502150327 1.2169761417494644 3.46701296154128 30 0 0.3560758306981181 1.7463460927585275 1.9712419748587076 4.147244322887026 31 1 0.645910533394866 0.4284330714261346 2.3586900073960435 4.3069849404644795 32 2 0.661101574877135 1.7387523607003186 1.6020759423043898 4.502201470393598 33 3 0.8359009992243358 0.6153376352549984 0.2072802397958522 1.8950719740007633 34 4 0.9986767032612425 1.1248994055437178 0.43892251806784766 3.4598462315003022 35 5 0.3714654920091779 1.8582259313901093 1.2657991421444619 4.445301397201582 36 6 0.4435184251425076 0.010143360630828102 0.26307562050780764 1.5634525012574971 37 7 0.0884559175669909 0.04185074324339655 2.5482243310741413 3.50181204437052 38 8 0.96792944945331 1.8409671989309215 1.3799983661711388 4.190487067264594 39 9 0.6093952359220532 0.822054391037446 0.8866699722812231 2.8643243441285726 40 0 0.4142428953380821 1.208052077632985 0.8510661668688272 2.566151846762413 41 1 0.9816952691713327 0.13760670285817866 2.534313031686005 3.7384658048774817 42 2 0.6371595229355252 0.26696480453981564 0.6511380276385074 2.1479112085280008 43 3 0.07389260861726588 0.5263485632617333 2.5967070803926493 3.8382859516063457 44 4 0.18066454292925227 0.8197489916485317 2.925592939159154 4.057852449354597 45 5 0.902330927568372 0.8939537129693833 0.3873794961970102 3.0342363400016152 46 6 0.6768166947925219 0.9338257927738027 1.6324976544409706 3.960838184909241 47 7 0.749496542458592 1.8639446373089956 0.14234807150301787 2.9529876282467575 48 8 0.7748820473462624 1.1799085373274103 0.23294127793053232 2.716357045866137 49 9




Define the return schema

In [0]:
train_return_schema = "device_id integer, n_used integer, model_path string, mse float"


## Define a *pandas* Function

Define a pandas function that takes all the data for a given device, train a model, saves it as a nested run, and returns a spark object with the above schema

In [0]:
import mlflow
import mlflow.sklearn
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error

def train_model(df_pandas: pd.DataFrame) -> pd.DataFrame:
    """
    Trains an sklearn model on grouped instances
    """
    # Pull metadata
    device_id = df_pandas["device_id"].iloc[0]
    n_used = df_pandas.shape[0]
    run_id = df_pandas["run_id"].iloc[0] # Pulls run ID to do a nested run

    # Train the model
    X = df_pandas[["feature_1", "feature_2", "feature_3"]]
    y = df_pandas["label"]
    rf = RandomForestRegressor()
    rf.fit(X, y)

    # Evaluate the model
    predictions = rf.predict(X)
    mse = mean_squared_error(y, predictions) # Note we could add a train/test split

    # Resume the top-level training
    with mlflow.start_run(run_id=run_id) as outer_run:
        # Small hack for running as a job
        experiment_id = outer_run.info.experiment_id
        print(f"Current experiment_id = {experiment_id}")

        # Create a nested run for the specific device
        with mlflow.start_run(run_name=str(device_id), nested=True, experiment_id=experiment_id) as run:
            mlflow.sklearn.log_model(rf, str(device_id))
            mlflow.log_metric("mse", mse)
            mlflow.set_tag("device", str(device_id))

            artifact_uri = f"runs:/{run.info.run_id}/{device_id}"
            # Create a return pandas DataFrame that matches the schema above
            return_df = pd.DataFrame([[device_id, n_used, artifact_uri, mse]], 
                                    columns=["device_id", "n_used", "model_path", "mse"])

    return return_df 



## Apply the *pandas* Function

Apply the pandas function to grouped data. 

Note that the way you would apply this in practice depends largely on where the data for inference is located. In this example, we'll reuse the training data which contains our device and run id's.

In [0]:
with mlflow.start_run(run_name="Training session for all devices") as run:
    run_id = run.info.run_id

    model_directories_df = (df
        .withColumn("run_id", f.lit(run_id)) # Add run_id
        .groupby("device_id")
        .applyInPandas(train_model, schema=train_return_schema)
        .cache()
    )

combined_df = df.join(model_directories_df, on="device_id", how="left")
display(combined_df)

device_id record_id feature_1 feature_2 feature_3 label n_used model_path mse 0 0 0.5913269812644489 1.112624479962482 0.9383567332587058 3.599200876731657 10000 runs:/af779da7d0f449a59df513faef788148/0 0.013517693 1 1 0.2472129573119317 1.339393994322151 0.36354489657515054 2.8284911486508206 10000 runs:/7ba333312f55447a8965b47c3bb986fa/1 0.013608545 2 2 0.05249232681429028 1.2435866204951875 1.48153079167651 2.899007213485999 10000 runs:/f4865b6c49364f518a9d289e5b91da10/2 0.013606665 3 3 0.36458761315688115 0.583744962019102 0.7329966016597367 2.165171666135468 10000 runs:/f1924115e5594d79862270d344b6d7b9/3 0.013553851 4 4 0.552657693182898 1.7127538422257746 1.4460135454232481 4.382039674422539 10000 runs:/92995879b7464e5681125569b684f62c/4 0.013987291 5 5 0.2731973411636208 1.2702604513854396 0.6874138777647782 2.395843585005227 10000 runs:/4fa2dac857d1408caf87f270365bf208/5 0.013939485 6 6 0.004520761335917056 1.2435503189591823 0.30919173138981304 2.0764288822250303 10000 runs:/659b376e2f0a401d879dd7ba3c227200/6 0.013189818 7 7 0.8191065070385846 0.34956610867400784 2.210135357499151 4.005836631215531 10000 runs:/36450efbf22e47be900804cdc1159314/7 0.0134388 8 8 0.9984137037595777 0.8510422700126778 2.5389794995472412 5.233024923012909 10000 runs:/ec80991be2b944d4af946ad87a64d4ee/8 0.013699838 9 9 0.2480896138905483 1.2971139690365017 1.9046794438060033 4.367748918180926 10000 runs:/37e991ce1dca4c429fab04150452a33c/9 0.013551955 0 10 0.7993587204447464 0.9496071751293982 0.9716470575072201 3.192090815718112 10000 runs:/af779da7d0f449a59df513faef788148/0 0.013517693 1 11 0.6294933662195203 1.321679146066587 1.897314445209496 4.4948571501827495 10000 runs:/7ba333312f55447a8965b47c3bb986fa/1 0.013608545 2 12 0.9022222044409527 0.44485056692308844 1.1238051714403847 2.5524705795156564 10000 runs:/f4865b6c49364f518a9d289e5b91da10/2 0.013606665 3 13 0.35331546536154745 0.46123252640733226 0.15177055154348928 1.5002508373463523 10000 runs:/f1924115e5594d79862270d344b6d7b9/3 0.013553851 4 14 0.9284481010133068 1.8752476396332964 1.6236642280554365 4.710951716756325 10000 runs:/92995879b7464e5681125569b684f62c/4 0.013987291 5 15 0.10268950917828068 1.4089971662510619 2.6325352798019384 4.825489574099577 10000 runs:/4fa2dac857d1408caf87f270365bf208/5 0.013939485 6 16 0.8424168156663638 1.7648663212880467 0.5884819083950933 4.128628695164525 10000 runs:/659b376e2f0a401d879dd7ba3c227200/6 0.013189818 7 17 0.7644918536430274 0.4695050621126722 0.8924839768993923 2.5207639672082816 10000 runs:/36450efbf22e47be900804cdc1159314/7 0.0134388 8 18 0.17378291220403685 1.7294691670005007 0.5459175037955648 2.514707959382351 10000 runs:/ec80991be2b944d4af946ad87a64d4ee/8 0.013699838 9 19 0.753112742058177 0.47027872355054257 2.1657587699996315 4.141008048549111 10000 runs:/37e991ce1dca4c429fab04150452a33c/9 0.013551955 0 20 0.20206847535845873 1.4533651926489255 2.1343334937634477 4.388630687001344 10000 runs:/af779da7d0f449a59df513faef788148/0 0.013517693 1 21 0.38129423776569327 0.6940469797271798 0.010877859521410627 1.4764811668173103 10000 runs:/7ba333312f55447a8965b47c3bb986fa/1 0.013608545 2 22 0.11425866414756869 0.05591141853773918 2.6047015653035968 2.9746133315436505 10000 runs:/f4865b6c49364f518a9d289e5b91da10/2 0.013606665 3 23 0.11030521139957328 1.7482853295127747 2.864963901207933 4.762889818419795 10000 runs:/f1924115e5594d79862270d344b6d7b9/3 0.013553851 4 24 0.8290851573280731 1.1197658638073715 0.01633550453387811 2.02080783631116 10000 runs:/92995879b7464e5681125569b684f62c/4 0.013987291 5 25 0.8580651283427368 0.18801153748954635 1.6615015257119419 3.452149761984669 10000 runs:/4fa2dac857d1408caf87f270365bf208/5 0.013939485 6 26 0.9142169533003828 1.4161960204788437 2.4769945671068454 5.0150669339257234 10000 runs:/659b376e2f0a401d879dd7ba3c227200/6 0.013189818 7 27 0.42815773462212103 1.028463075884599 2.0715659231316463 4.474465672556487 10000 runs:/36450efbf22e47be900804cdc1159314/7 0.0134388 8 28 0.09661065420940729 1




Define a pandas function and return schema to apply the model.  *This needs only one read from DBFS per device.*

In [0]:
apply_return_schema = "record_id integer, prediction float"

def apply_model(df_pandas: pd.DataFrame) -> pd.DataFrame:
    """
    Applies model to data for a particular device, represented as a pandas DataFrame
    """
    model_path = df_pandas["model_path"].iloc[0]

    input_columns = ["feature_1", "feature_2", "feature_3"]
    X = df_pandas[input_columns]

    model = mlflow.sklearn.load_model(model_path)
    prediction = model.predict(X)

    return_df = pd.DataFrame({
        "record_id": df_pandas["record_id"],
        "prediction": prediction
    })
    return return_df

prediction_df = combined_df.groupby("device_id").applyInPandas(apply_model, schema=apply_return_schema)
display(prediction_df)

record_id prediction 0 3.3567488 10 3.1955097 20 4.3956113 30 4.244173 40 2.777165 50 5.8057604 60 4.0739546 70 4.0036645 80 4.7343607 90 1.92923 100 2.8150811 110 3.806385 120 4.293821 130 3.8328235 140 3.823021 150 2.284847 160 3.60691 170 2.6467009 180 2.7297986 190 5.6064353 200 2.371093 210 3.221862 220 2.8206556 230 2.2814574 240 4.585701 250 4.293064 260 3.579702 270 3.5997193 280 3.6257029 290 4.0717196 300 4.120893 310 3.6187255 320 1.7139564 330 2.2295475 340 5.1575985 350 3.3295221 360 4.0245934 370 3.4155116 380 2.1121812 390 4.6880126 400 3.3825562 410 1.6056256 420 1.8525511 430 2.8112018 440 4.4285126 450 3.0463884 460 2.331469 470 2.763207 480 4.5865984 490 4.092507 500 1.6729816 510 4.721688 520 4.760369 530 1.9098423 540 3.6533883 550 4.141096 560 2.1474276 570 1.7054383 580 4.6003942 590 3.5176134 600 4.189418 610 2.7845285 620 4.443068 630 3.522676 640 3.3253584 650 2.3704443 660 2.725698 670 2.4127495 680 2.9071825 690 1.2406396 700 2.9632132 710 3.784885 720 2.7353058 730 4.9108047 740 2.2826076 750 5.5414395 760 3.0618317 770 3.7765384 780 5.217087 790 3.5016985 800 3.75516 810 2.1743035 820 4.845552 830 4.1410136 840 3.5180445 850 2.4078846 860 2.9760141 870 2.1771066 880 4.476535 890 4.2423124 900 4.5798216 910 3.0181618 920 3.8302503 930 4.812197 940 2.6297674 950 3.3629317 960 4.266781 970 3.8543983 980 5.0554023 990 1.8584133 1000 3.6255407 1010 4.134565 1020 5.280326 1030 1.9040649 1040 4.753112 1050 2.0200355 1060 3.4752655 1070 4.6386533 1080 1.8487008 1090 3.4927866 1100 2.973128 1110 4.2826734 1120 1.979653 1130 3.6664882 1140 3.907116 1150 4.1313257 1160 4.6889734 1170 4.9848456 1180 0.6373504 1190 5.7177577 1200 2.9557257 1210 2.1905253 1220 3.1736832 1230 2.6142712 1240 2.0835524 1250 4.341003 1260 4.952206 1270 4.91967 1280 2.5199194 1290 4.45571 1300 3.2773821 1310 3.839859 1320 2.6487978 1330 5.897995 1340 2.966327 1350 1.7208079 1360 1.5188752 1370 3.691809 1380 2.475056 1390 6.0652776 1400 2.4943366 1410 4.8061776 1420 4.6739645 1430 1.592073 1440 3.2158666 1450 0.5976804 1460 2.7308428 1470 2.6984484 1480 3.6533837 1490 3.4229684 1500 4.8472543 1510 4.709904 1520 3.4508958 1530 4.0557094 1540 2.6984181 1550 2.5650086 1560 4.2013955 1570 3.5575202 1580 4.798287 1590 3.7149832 1600 4.626862 1610 3.962209 1620 5.360096 1630 3.3171144 1640 5.0426297 1650 3.4025428 1660 4.9844255 1670 1.1902127 1680 4.6920757 1690 2.9167335 1700 1.9629763 1710 3.939721 1720 4.3267846 1730 3.7024412 1740 2.3138516 1750 2.4477792 1760 3.3313634 1770 2.774589 1780 3.9063454 1790 4.195966 1800 3.6233134 1810 3.1009479 1820 2.8943582 1830 4.0635715 1840 3.833562 1850 4.039639 1860 3.412217 1870 2.6474652 1880 3.352098 1890 2.9955153 1900 4.8679543 1910 3.4037616 1920 1.8724161 1930 1.5265434 1940 5.1718655 1950 1.9027773 1960 2.7392871 1970 3.1711526 1980 1.89972 1990 3.7914953 2000 2.9884322 2010 3.6552353 2020 1.0150644 2030 3.1581807 2040 4.754503 2050 3.206482 2060 4.7705092 2070 4.9572525 2080 3.0099995 2090 2.1948688 2100 3.5402288 2110 2.761854 2120 1.829221 2130 1.5811139 2140 4.6340137 2150 3.8655684 2160 2.2706254 2170 4.665048 2180 4.079977 2190 3.4311237 2200 3.7276492 2210 3.9657185 2220 3.4467978 2230 3.4704626 2240 3.3232803 2250 2.8021953 2260 3.193579 2270 4.7041583 2280 3.6385555 2290 4.8542356 2300 3.4812217 2310 4.5128546 2320 5.147165 2330 3.8293417 2340 1.9889377 2350 2.4695554 2360 3.262229 2370 4.7779856 2380 3.5824845 2390 2.6682253 2400 2.8322241 2410 3.3683836 2420 1.9681858 2430 3.8999496 2440 2.6007352 2450 2.5829616 2460 4.9011655 2470 5.051584 2480 1.833509 2490 3.655778 2500 3.504239 2510 4.2740383 2520 4.9106674 2530 5.039733 2540 4.2274404 2550 3.333818 2560 3.9499676 2570 2.838692 2580 2.7178414 2590 3.1689117 2600 2.3344429 2610 3.0256636 2620 2.879213 2630 4.3101163 2640 2.7155242 2650 3.3895757 2660 2.6857653 2670 3.172986 2680 5.452668 2690 3.0986552 2700 3.733607 2710 2.9728808 2720 3.4577541 2730 3.0828664 2740 4.3800836 2750 3.19389 2760 3.0406477 2770 1.2063053 2780 5.1




## Serving Multiple Models from a Registered Model

MLflow allows models to deploy as real-time REST APIs. At the moment, a single MLflow model serves from one instance (typically one VM). However, sometimes multiple models need to be served from a single endpoint. Imagine 1000 similar models that need to be served with different inputs. Running 1000 endpoints could waste resources, especially if certain models are underutilized.

One way around this is to package many models into a single custom model, which internally routes to one of the models based on the input and deploys that 'bundle' of models as a single 'model.'

Below we demonstrate creating such a custom model that bundles all of the models we trained for each device. For every row of data fed to this model, the model will determine the device id and then use the appropriate model trained on that device id to make predictions for a given row. 

First, we need to access the models for each device id.

In [0]:
experiment_id = run.info.experiment_id

model_df = (spark.read.format("mlflow-experiment")
            .load(experiment_id)
            .filter("tags.device IS NOT NULL")
            .orderBy("end_time", ascending=False)
            .select("tags.device", "run_id")
            .limit(10))

display(model_df)

device run_id 2 f4865b6c49364f518a9d289e5b91da10 4 92995879b7464e5681125569b684f62c 8 ec80991be2b944d4af946ad87a64d4ee 5 4fa2dac857d1408caf87f270365bf208 1 7ba333312f55447a8965b47c3bb986fa 3 f1924115e5594d79862270d344b6d7b9 9 37e991ce1dca4c429fab04150452a33c 6 659b376e2f0a401d879dd7ba3c227200 0 af779da7d0f449a59df513faef788148 7 36450efbf22e47be900804cdc1159314




We create a dictionary mapping device ids to the model trained on that device id.

In [0]:
device_to_model = {row["device"]: mlflow.sklearn.load_model(f"runs:/{row['run_id']}/{row['device']}") for row in model_df.collect()}
                                                          
device_to_model

Out[11]: {'2': RandomForestRegressor(),
 '4': RandomForestRegressor(),
 '8': RandomForestRegressor(),
 '5': RandomForestRegressor(),
 '1': RandomForestRegressor(),
 '3': RandomForestRegressor(),
 '9': RandomForestRegressor(),
 '6': RandomForestRegressor(),
 '0': RandomForestRegressor(),
 '7': RandomForestRegressor()}




We create a custom model that takes the device id to model mappings as an attribute and delegates input to the appropriate model based on the device id.

In [0]:
from mlflow.pyfunc import PythonModel

class OriginDelegatingModel(PythonModel):
    
    def __init__(self, device_to_model_map):
        self.device_to_model_map = device_to_model_map
        
    def predict_for_device(self, row):
        '''
        This method applies to a single row of data by
        fetching the appropriate model and generating predictions
        '''
        model = self.device_to_model_map.get(str(row["device_id"]))
        data = row[["feature_1", "feature_2", "feature_3"]].to_frame().T
        return model.predict(data)[0]
    
    def predict(self, model_input):
        return model_input.apply(self.predict_for_device, axis=1)




Here we demonstrate the use of this model.

In [0]:
example_model = OriginDelegatingModel(device_to_model)
example_model.predict(combined_df.toPandas().head(20))

Out[13]: 0     3.356749
1     2.785805
2     3.108209
3     2.143637
4     4.388737
5     2.559558
6     2.022091
7     3.901708
8     4.986222
9     4.193384
10    3.195510
11    4.470499
12    2.669877
13    1.439910
14    4.875395
15    4.658165
16    3.996539
17    2.561680
18    2.754425
19    4.023048
dtype: float64




From here we can log and then register the model to be used for serving models for all the device ids from one instance.

In [0]:
with mlflow.start_run():
    model = OriginDelegatingModel(device_to_model)
    mlflow.pyfunc.log_model("model", python_model=model)

/databricks/python/lib/python3.9/site-packages/_distutils_hack/__init__.py:30: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")



## Classroom Cleanup

Run the following cell to remove lessons-specific assets created during this lesson:

In [0]:
DA.cleanup()

Resetting the learning environment:
| dropping the schema "charlie_ohara_4mi2_da_sml"...(1 seconds)
| removing the working directory "dbfs:/mnt/dbacademy-users/charlie.ohara@standard.ai/scalable-machine-learning-with-apache-spark"...(0 seconds)

Validating the locally installed datasets:
| listing local files...(3 seconds)
| validation completed...(3 seconds total)


&copy; 2023 Databricks, Inc. All rights reserved.<br/>
Apache, Apache Spark, Spark and the Spark logo are trademarks of the <a href="https://www.apache.org/">Apache Software Foundation</a>.<br/>
<br/>
<a href="https://databricks.com/privacy-policy">Privacy Policy</a> | <a href="https://databricks.com/terms-of-use">Terms of Use</a> | <a href="https://help.databricks.com/">Support</a>